# Set up

In [1]:
import json
import pandas as pd
import numpy as np
import os
import sys
import tensorflow as tf
from time import time
import io
import re

import pickle
from csv import reader
import matplotlib.pyplot as plt

import matplotlib.pyplot as plt
from matplotlib import colors
from matplotlib.ticker import PercentFormatter

from tensorflow.keras import layers
from tensorflow.keras.backend import sparse_categorical_crossentropy
from tensorflow.keras.layers import Dense, Flatten
from tensorflow.keras.utils import plot_model

# physical_devices = tf.config.list_physical_devices('GPU') 
# tf.config.experimental.set_memory_growth(physical_devices[0], True)

from datetime import datetime
from collections import defaultdict

from sklearn.model_selection import train_test_split



In [2]:
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

Num GPUs Available:  1


In [3]:
tf.config.list_physical_devices()

[PhysicalDevice(name='/physical_device:CPU:0', device_type='CPU'),
 PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]

In [4]:
from transformers import TFXLNetForSequenceClassification, XLNetTokenizer

In [5]:
# set up 

# label encoder
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()

# nn stuff
tokenizer_transformer = XLNetTokenizer.from_pretrained('xlnet-large-cased')
MAX_LEN = 512

# tfidf stuff
import pickle
# train_dataset = pickle.load(open("vectorized_train.pickle", "rb"))
# val_dataset = pickle.load(open("vectorized_val.pickle", "rb"))
# tf-idf from https://stackabuse.com/text-classification-with-python-and-scikit-learn/
from sklearn.feature_extraction.text import CountVectorizer

# vectorizer = CountVectorizer(max_features=1500, min_df=5, max_df=0.7, stop_words=stopwords.words('english'))
# trainX = vectorizer.fit_transform(train_dataset).toarray()
# valX = vectorizer.transform(val_dataset).toarray()
vectorizer = pickle.load(open("vectorizersourcelevel.pickle", "rb"))

from sklearn.feature_extraction.text import TfidfTransformer
# tfidfconverter = TfidfTransformer()
# trainX = tfidfconverter.fit_transform(trainX).toarray()
# valX = tfidfconverter.transform(valX).toarray()
tfidfconverter = pickle.load(open("tfidfconverter.pickle", "rb"))


## Methods

In [6]:
# nn methods

def create_input_array(sentences, tokenizer):
#     sentences = df.content.values

    input_ids = []
    attention_masks = []
    token_type_ids = []

    for sent in sentences:
        # `encode_plus` will:
        #   (1) Tokenize the sentence.
        #   (2) Prepend the `[CLS]` token to the start.
        #   (3) Append the `[SEP]` token to the end.
        #   (4) Map tokens to their IDs.
        #   (5) Pad or truncate the sentence to `max_length`
        #   (6) Create attention masks for [PAD] tokens.
        encoded_dict = tokenizer.encode_plus(
            sent,  # Sentence to encode.
            add_special_tokens=True,  # Add '[CLS]' and '[SEP]'
            max_length=MAX_LEN,  # Pad & truncate all sentences.
                pad_to_max_length=True,
                return_attention_mask=True,  # Construct attn. masks.
                return_tensors='tf',  # Return tf tensors.
            )

        # Add the encoded sentence to the list.
        input_ids.append(encoded_dict['input_ids'])

        # And its attention mask (simply differentiates padding from non-padding).
        attention_masks.append(encoded_dict['attention_mask'])

        token_type_ids.append(encoded_dict['token_type_ids'])

    input_ids = tf.convert_to_tensor(input_ids)
    attention_masks = tf.convert_to_tensor(attention_masks)
    token_type_ids = tf.convert_to_tensor(token_type_ids)


    return input_ids, attention_masks, token_type_ids
#     return input_ids, attention_masks

def convert_inputs_to_tf_dataset(inputs):
    # args.max_seq_len = 256
    ids = inputs[0][0]
    masks = inputs[0][1]
    token_types = inputs[0][2]

    ids = tf.reshape(ids, (-1, MAX_LEN))
#     print("Input ids shape: ", ids.shape)
    masks = tf.reshape(masks, (-1, MAX_LEN))
#     print("Input Masks shape: ", masks.shape)
    token_types = tf.reshape(token_types, (-1, MAX_LEN))
#     print("Token type ids shape: ", token_types.shape)

    ids=ids.numpy()
    masks = masks.numpy()
    token_types = token_types.numpy()
#     return[ids]
#     return [ids, masks, token_types]
    return [ids, masks]



In [32]:
def get_nn_probs(text, model):
    
# pred_probs = []
    text_input = [text]
#     test_labels = np.asarray(le.fit_transform(test_section['bias_text']))

    text_inputs = [create_input_array(text_input, tokenizer=tokenizer_transformer)]
    text_data = convert_inputs_to_tf_dataset(text_inputs)
#     model = TFXLNetForSequenceClassification.from_pretrained("data/experiments/XLNetmodellarge", num_labels=3)
#     loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
#     metric = tf.keras.metrics.SparseCategoricalAccuracy('accuracy')
#     optimizer = tf.keras.optimizers.Adam(learning_rate=2e-07, epsilon=1e-08)

#     model.compile(optimizer=optimizer, loss=loss, metrics=[metric])

#     test_probs = testmodel.predict_on_batch(test_data, batch_size= 5, verbose=0)
    nn_output = model.predict_on_batch(text_data)
    nn_logits = nn_output["logits"]
#     nn_probs = list(np.array(tf.nn.softmax(nn_logits)))
    nn_probs = np.array(tf.nn.softmax(nn_logits)).tolist()
    return nn_probs[0]
   


In [8]:
def get_tfidf_probs(text):
    
    text_input = [text]
    vect = vectorizer.transform(text_input).toarray()
    tfidfmatrix = tfidfconverter.transform(vect).toarray()
    
    # sourcelvl
    clf = pickle.load(open("clfsourcelevel.pickle", "rb"))
    tfidf_probs = clf.predict_proba(tfidfmatrix).tolist()
    
    return tfidf_probs[0]

In [21]:
def compare_probs(nn_probs, tfidf_probs):
    
    nn_prob = max(nn_probs)
    nn_label = nn_probs.index(nn_prob)
    
    tfidf_prob = max(tfidf_probs)
    tfidf_label = tfidf_probs.index(tfidf_prob)
    
    if tfidf_prob >= nn_prob:
        return tfidf_label, tfidf_prob
    return nn_label, nn_prob

In [41]:
def hybrid_model(text, m=None):
    
    if m is None:
        xlnet = TFXLNetForSequenceClassification.from_pretrained("data/experiments/XLNetmodellarge", num_labels=3)
        loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
        metric = tf.keras.metrics.SparseCategoricalAccuracy('accuracy')
        optimizer = tf.keras.optimizers.Adam(learning_rate=2e-07, epsilon=1e-08)
        xlnet.compile(optimizer=optimizer, loss=loss, metrics=[metric])
        m = xlnet
        
    nn_probs = get_nn_probs(text, m)
    
    tfidf_probs = get_tfidf_probs(text)
    
    label, prob = compare_probs(nn_probs, tfidf_probs)
    
#     tf.keras.backend.clear_session()
        
    return label, prob, nn_probs, tfidf_probs
        
    

In [42]:
def iterate_on_data(test_data):
    label_list = []
    prob_list = []
    nn_prob_list = []
    tfidf_prob_list = []
    
    xlnet = TFXLNetForSequenceClassification.from_pretrained("data/experiments/XLNetmodellarge", num_labels=3)
    loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
    metric = tf.keras.metrics.SparseCategoricalAccuracy('accuracy')
    optimizer = tf.keras.optimizers.Adam(learning_rate=2e-07, epsilon=1e-08)
    xlnet.compile(optimizer=optimizer, loss=loss, metrics=[metric])
        
    for i in range(len(test_data)):
        label, prob, nn_probs, tfidf_probs = hybrid_model(test_data[i], xlnet)
        print(label)
        print(prob)
        label_list.append(label)
        prob_list.append(prob)
        nn_prob_list.append(nn_probs)
        tfidf_prob_list.append(tfidf_probs)
        
    return [label_list, prob_list, nn_prob_list, tfidf_prob_list]

### Testing

In [35]:
# ex = "I hate blue cheese, and so does France.  Why do they make it then?  Democrats"
# result = get_nn_probs(ex)

In [13]:
result

[0.004696231801062822, 0.05842537805438042, 0.9368784427642822]

In [14]:
ex = "I hate blue cheese, and so does France.  Why do they make it then?  Democrats"
result = get_tfidf_probs(ex)

In [15]:
result

[0.25006879543686206, 0.2950477770266745, 0.4548834275364623]

In [36]:
hybrid_model(ex)

All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


(2,
 0.9368784427642822,
 [0.004696231801062822, 0.05842537805438042, 0.9368784427642822],
 [0.25006879543686206, 0.2950477770266745, 0.4548834275364623])

# Iterating

### Source level data

In [17]:
sourcetest = pd.read_table("sourcelevel_test_dataset.csv", index_col=0)
sourcetest

topic            source  bias  \
0           palestine    Breitbart News     2   
1      federal_budget          ABC News     0   
2                 fbi           Reuters     1   
3            politics               CBN     2   
4          media_bias    Breitbart News     2   
...               ...               ...   ...   
1295         politics               CBN     2   
1296              fbi             Salon     0   
1297         politics           Newsmax     2   
1298       media_bias  The Daily Caller     2   
1299  race_and_racism  Associated Press     1   

                                                    url  \
0     http://www.breitbart.com/big-journalism/2015/0...   
1     http://abcnews.go.com/blogs/politics/2013/03/w...   
2     https://www.reuters.com/article/us-usa-trump-r...   
3     http://www1.cbn.com/cbnnews/politics/2019/febr...   
4     http://www.breitbart.com/big-government/2017/0...   
...                                                 ...   
1295  http://www1.cbn.com/cbnnews/politics/2018/augu...   
1296  http://www.salon.com/2017/05/10/the-fbi-is-ree...   
1297  http://www.newsmax.com/Newsfront/loretta-lynch...   
1298  http://dailycaller.com/2016/11/30/fake-news-me...   
1299  https://apnews.com/697d654ea64f3370f373aacfca2...   

                                                  title        date  \
0     Obama, Media Lied About Netanyahu and the Pale...  2015-03-20   
1     Will Fractured House Republicans Unite on Budget?         NaN   
2     Trump blocks release of Russia memo drafted by...  2018-02-10   
3     Trump's North Korea Peace Talks Share Spotligh...  2019-02-25   
4     Six Times President Trump Upset Jared Kushner ...  2017-08-20   
...                                                 ...         ...   
1295  America 'Was Never that Great': NY Gov. Andrew...  2018-08-16   
1296  The FBI is reeling from shock of Comey’s unexp...  2017-05-10   
1297  Human-Trafficking Bill Fight Could Hold Up Lor...  2015-03-15   
1298  Fake News: Media Pushes Bogus Survey As Proof ...  2016-11-30   
1299  US cities gird for more violence as Trump decr...  2020-06-02   

                        authors  \
0                   Ben Shapiro   
1                John Parkinson   
2                 Ayesha Rascoe   
3                           NaN   
4                     Adam Shaw   
...                         ...   
1295                        NaN   
1296              Matthew Rozsa   
1297                        NaN   
1298                        NaN   
1299  Zeke Miller, Tim Sullivan   

                                                content  \
0     For the last several days , the entire Western...   
1     Tomorrow morning , House Budget Chairman Paul ...   
2     WASHINGTON ( ███ ) - President Donald Trump on...   
3     President Donald Trump arrives in Hanoi , Viet...   
4     President Trump ’ s fiery response to the even...   
...                                                 ...   
1295  New York Gov . Andrew Cuomo surprised an audie...   
1296  Agents who work for the FBI are reported to be...   
1297  The U.S. Senate majority leader said Sunday he...   
1298  Multiple U.S. media outlets are citing an onli...   
1299  With the White House in the background , a lin...   

                                       content_original           source_url  \
0     For the last several days, the entire Western ...    www.breitbart.com   
1     Jacquelyn Martin/AP Photo\n\nTomorrow morning,...   www.abcnews.go.com   
2     WASHINGTON (Reuters) - President Donald Trump ...      www.reuters.com   
3     President Donald Trump arrives in Hanoi, Vietn...         www1.cbn.com   
4     President Trump’s fiery response to the events...    www.breitbart.com   
...                                                 ...                  ...   
1295  New York Gov. Andrew Cuomo surprised an audien...         www1.cbn.com   
1296  Agents who work for the FBI are reported to be...        www.salon.com   
1297  The U.S. 

In [22]:
sourcetext = list(sourcetest["content"])

In [23]:
len(sourcetext)

1300

In [24]:
hybrid_model_output = iterate_on_data(sourcetext)

/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


2
0.932278037071228


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


0
0.5546085238456726


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


...

0
0.978195309638977


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


1
0.7243269681930542


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


0
0.9960203766822815


In [27]:
labels = hybrid_model_output[0]
probs = hybrid_model_output[1]
nn_probs = hybrid_model_output[2]
tf_idf_probs = hybrid_model_output[3]

In [29]:
sourcetest["hybrid_label"] = pd.Series(labels)
sourcetest["hybrid_prob"] = pd.Series(probs)
sourcetest["hybrid_nn_probs"] = pd.Series(nn_probs)
sourcetest["hybrid_tfidf_probs"] = pd.Series(tf_idf_probs)
sourcetest.head()

topic          source  bias  \
0       palestine  Breitbart News     2   
1  federal_budget        ABC News     0   
2             fbi         Reuters     1   
3        politics             CBN     2   
4      media_bias  Breitbart News     2   

                                                 url  \
0  http://www.breitbart.com/big-journalism/2015/0...   
1  http://abcnews.go.com/blogs/politics/2013/03/w...   
2  https://www.reuters.com/article/us-usa-trump-r...   
3  http://www1.cbn.com/cbnnews/politics/2019/febr...   
4  http://www.breitbart.com/big-government/2017/0...   

                                               title        date  \
0  Obama, Media Lied About Netanyahu and the Pale...  2015-03-20   
1  Will Fractured House Republicans Unite on Budget?         NaN   
2  Trump blocks release of Russia memo drafted by...  2018-02-10   
3  Trump's North Korea Peace Talks Share Spotligh...  2019-02-25   
4  Six Times President Trump Upset Jared Kushner ...  2017-08-20   

          authors                                            content  \
0     Ben Shapiro  For the last several days , the entire Western...   
1  John Parkinson  Tomorrow morning , House Budget Chairman Paul ...   
2   Ayesha Rascoe  WASHINGTON ( ███ ) - President Donald Trump on...   
3             NaN  President Donald Trump arrives in Hanoi , Viet...   
4       Adam Shaw  President Trump ’ s fiery response to the even...   

                                    content_original          source_url  \
0  For the last several days, the entire Western ...   www.breitbart.com   
1  Jacquelyn Martin/AP Photo\n\nTomorrow morning,...  www.abcnews.go.com   
2  WASHINGTON (Reuters) - President Donald Trump ...     www.reuters.com   
3  President Donald Trump arrives in Hanoi, Vietn...        www1.cbn.com   
4  President Trump’s fiery response to the events...   www.breitbart.com   

  bias_text                ID  pred_labels  hybrid_label  hybrid_prob  \
0     right  uI2K5BSCO0LaWuKb            4             2     0.932278   
1      left  zeSfcxLilzR0R1Dt            4             0     0.554609   
2    center  ru8kAxfdPzZc11le            4             0     0.999660   
3     right  TTt5FFmsW6ng3fsC            4             0     0.947262   
4     right  gYKaZGjLCYdEghTZ            4             2     0.998557   

                                     hybrid_nn_probs  \
0  [0.005442489869892597, 0.06227951869368553, 0....   
1  [0.5546085238456726, 0.19034647941589355, 0.25...   
2  [0.9996604919433594, 6.564209616044536e-05, 0....   
3  [0.9472617506980896, 0.0005362341180443764, 0....   
4  [0.000647720939014107, 0.0007950758445076644, ...   

                                  hybrid_tfidf_probs  
0  [0.2019185656148889, 0.33856253449073165, 0.45...  
1  [0.22396259845512798, 0.3365162631639265, 0.43...  
2  [0.33335247222947717, 0.25433261654571443, 0.4...  
3  [0.2630276689756886, 0.29193362807534673, 0.44...  
4  [0.30407980649538496, 0.27718891923173106, 0.4...

In [30]:
sourcetest.to_csv("sourcetestdata_hybridoutput.csv", index=False)

In [31]:
sourcetestdata_hybridoutput = pd.read_csv("sourcetestdata_hybridoutput.csv")
sourcetestdata_hybridoutput.head()

topic          source  bias  \
0       palestine  Breitbart News     2   
1  federal_budget        ABC News     0   
2             fbi         Reuters     1   
3        politics             CBN     2   
4      media_bias  Breitbart News     2   

                                                 url  \
0  http://www.breitbart.com/big-journalism/2015/0...   
1  http://abcnews.go.com/blogs/politics/2013/03/w...   
2  https://www.reuters.com/article/us-usa-trump-r...   
3  http://www1.cbn.com/cbnnews/politics/2019/febr...   
4  http://www.breitbart.com/big-government/2017/0...   

                                               title        date  \
0  Obama, Media Lied About Netanyahu and the Pale...  2015-03-20   
1  Will Fractured House Republicans Unite on Budget?         NaN   
2  Trump blocks release of Russia memo drafted by...  2018-02-10   
3  Trump's North Korea Peace Talks Share Spotligh...  2019-02-25   
4  Six Times President Trump Upset Jared Kushner ...  2017-08-20   

          authors                                            content  \
0     Ben Shapiro  For the last several days , the entire Western...   
1  John Parkinson  Tomorrow morning , House Budget Chairman Paul ...   
2   Ayesha Rascoe  WASHINGTON ( ███ ) - President Donald Trump on...   
3             NaN  President Donald Trump arrives in Hanoi , Viet...   
4       Adam Shaw  President Trump ’ s fiery response to the even...   

                                    content_original          source_url  \
0  For the last several days, the entire Western ...   www.breitbart.com   
1  Jacquelyn Martin/AP Photo\n\nTomorrow morning,...  www.abcnews.go.com   
2  WASHINGTON (Reuters) - President Donald Trump ...     www.reuters.com   
3  President Donald Trump arrives in Hanoi, Vietn...        www1.cbn.com   
4  President Trump’s fiery response to the events...   www.breitbart.com   

  bias_text                ID  pred_labels  hybrid_label  hybrid_prob  \
0     right  uI2K5BSCO0LaWuKb            4             2     0.932278   
1      left  zeSfcxLilzR0R1Dt            4             0     0.554609   
2    center  ru8kAxfdPzZc11le            4             0     0.999660   
3     right  TTt5FFmsW6ng3fsC            4             0     0.947262   
4     right  gYKaZGjLCYdEghTZ            4             2     0.998557   

                                     hybrid_nn_probs  \
0  [0.005442489869892597, 0.06227951869368553, 0....   
1  [0.5546085238456726, 0.19034647941589355, 0.25...   
2  [0.9996604919433594, 6.564209616044536e-05, 0....   
3  [0.9472617506980896, 0.0005362341180443764, 0....   
4  [0.000647720939014107, 0.0007950758445076644, ...   

                                  hybrid_tfidf_probs  
0  [0.2019185656148889, 0.33856253449073165, 0.45...  
1  [0.22396259845512798, 0.3365162631639265, 0.43...  
2  [0.33335247222947717, 0.25433261654571443, 0.4...  
3  [0.2630276689756886, 0.29193362807534673, 0.44...  
4  [0.30407980649538496, 0.27718891923173106, 0.4...

### Article level data

In [43]:
articletest = pd.read_table("test_dataset.csv", index_col=0)
articletest

index                                                url       q3  \
0         2  http://www.washingtonpost.com/opinions/dont-le...  Opinion   
1         4  http://www.breitbart.com/Big-Government/2013/1...  Opinion   
2         8  http://www.dailykos.com/story/2013/12/02/12595...     News   
3         9  http://www.nytimes.com/2013/05/24/us/politics/...     News   
4        11  http://www.latimes.com/news/local/la-me-cap-gu...    other   
...     ...                                                ...      ...   
8345  12345  http://www.washingtonpost.com/opinions/dana-mi...     News   
8346  12346  http://news.yahoo.com/republicans-hatred-obama...  Opinion   
8347  12347  http://www.washingtonpost.com/opinions/dana-mi...     News   
8348  12348  http://www.washingtonpost.com/opinions/ej-dion...     News   
8349  12349  http://www.huffingtonpost.com/2013/08/11/this-...  Opinion   

      perceived        primary.topic      secondary.topic     democrat.vote  \
0             1         Civil Rights         Civil Rights           Neutral   
1             1         Civil Rights         Civil Rights           Neutral   
2             1         Civil Rights         Civil Rights  SomewhatPositive   
3             1         Civil Rights         Civil Rights           Neutral   
4             0         Civil Rights         Civil Rights           Neutral   
...         ...                  ...                  ...               ...   
8345          1  Republican Scandals  Republican Scandals  SomewhatPositive   
8346          1  Republican Scandals  Republican Scandals  SomewhatPositive   
8347          1  Republican Scandals  Republican Scandals           Neutral   
8348          1  Republican Scandals  Republican Scandals  SomewhatPositive   
8349          1  Republican Scandals  Republican Scandals  SomewhatPositive   

       republican.vote                                            article  \
0              Neutral  david cole is a professor of constitutional la...   
1              Neutral  u.s. immigration citizenship and immigration s...   
2     SomewhatNegative              the following irresponsible police...   
3              Neutral  an alternative possibility is that a bipartisa...   
4     SomewhatPositive  sacramento — “living in parallel universes,” i...   
...                ...                                                ...   
8345  SomewhatNegative  president obama won reelection in part by beat...   
8346  SomewhatNegative  red-faced republicans, circling and preparing ...   
8347           Neutral  rep. steve stockman’s moment as a viable senat...   
8348  SomewhatNegative  we interrupt this highly partisan and ideologi...   
8349  SomewhatNegative  file - in this sept. 27, 2012 file photo, dona...   

      length  democrat.bias  republican.bias              biaslabel  isbiased  \
0        600            0.0              0.0                Neutral         0   
1        600            0.0              0.0                Neutral         0   
2        498            0.5             -0.5                Liberal         1   
3        372            0.0              0.0                Neutral         0   
4        600            0.0              0.5  Somewhat Conservative         1   
...      ...            ...              ...                    ...       ...   
8345     600            0.5             -0.5                Liberal         1   
8346     600            0.5             -0.5                Liberal         1   
8347     600            0.0              0.0                Neutral         0   
8348     600            0.5             -0.5                Liberal         1   
8349     358            0.5             -0.5                Liberal         1   

      biascategories  bias_magnitude bias_text  \
0                  0             0.0    center   
1                  0             0.0    center   
2                  1             1.0      left   
3                  0             0.0    center   
4       

In [44]:
articletext = list(articletest["article"])
len(articletext)

8350

In [45]:
hybrid_model_articlelvl_output = iterate_on_data(articletext)

All model checkpoint layers were used when initializing TFXLNetForSequenceClassification.

All the layers of TFXLNetForSequenceClassification were initialized from the model checkpoint at data/experiments/XLNetmodellarge.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLNetForSequenceClassification for predictions without further training.


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


1
0.9984557628631592


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


2
0.9964563250541687


...

1
0.9980067610740662


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


1
0.8979237079620361


/usr/local/lib/python3.8/dist-packages/transformers/tokenization_utils_base.py:2126: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


1
0.9717759490013123


In [46]:
labels = hybrid_model_articlelvl_output[0]
probs = hybrid_model_articlelvl_output[1]
nn_probs = hybrid_model_articlelvl_output[2]
tf_idf_probs = hybrid_model_articlelvl_output[3]

In [47]:
articletest["hybrid_label"] = pd.Series(labels)
articletest["hybrid_prob"] = pd.Series(probs)
articletest["hybrid_nn_probs"] = pd.Series(nn_probs)
articletest["hybrid_tfidf_probs"] = pd.Series(tf_idf_probs)
articletest.head()

index                                                url       q3  \
0      2  http://www.washingtonpost.com/opinions/dont-le...  Opinion   
1      4  http://www.breitbart.com/Big-Government/2013/1...  Opinion   
2      8  http://www.dailykos.com/story/2013/12/02/12595...     News   
3      9  http://www.nytimes.com/2013/05/24/us/politics/...     News   
4     11  http://www.latimes.com/news/local/la-me-cap-gu...    other   

   perceived primary.topic secondary.topic     democrat.vote  \
0          1  Civil Rights    Civil Rights           Neutral   
1          1  Civil Rights    Civil Rights           Neutral   
2          1  Civil Rights    Civil Rights  SomewhatPositive   
3          1  Civil Rights    Civil Rights           Neutral   
4          0  Civil Rights    Civil Rights           Neutral   

    republican.vote                                            article  \
0           Neutral  david cole is a professor of constitutional la...   
1           Neutral  u.s. immigration citizenship and immigration s...   
2  SomewhatNegative              the following irresponsible police...   
3           Neutral  an alternative possibility is that a bipartisa...   
4  SomewhatPositive  sacramento — “living in parallel universes,” i...   

   length  ...  isbiased  biascategories bias_magnitude  bias_text  \
0     600  ...         0               0            0.0     center   
1     600  ...         0               0            0.0     center   
2     498  ...         1               1            1.0       left   
3     372  ...         0               0            0.0     center   
4     600  ...         1              -1            0.5      right   

                                             content  pred_labels  \
0  david cole is a professor of constitutional la...            1   
1  u.s. immigration citizenship and immigration s...            2   
2              the following irresponsible police...            2   
3  an alternative possibility is that a bipartisa...            1   
4  sacramento — “living in parallel universes,” i...            1   

  hybrid_label hybrid_prob                                    hybrid_nn_probs  \
0            1    0.998456  [0.000621203682385385, 0.9984557628631592, 0.0...   
1            2    0.996456  [0.00017927114095073193, 0.003364395350217819,...   
2            2    0.981165  [0.00046024733455851674, 0.018374672159552574,...   
3            1    0.998758  [0.0005090124905109406, 0.9987584352493286, 0....   
4            1    0.536058  [0.002071336144581437, 0.5360579490661621, 0.4...   

                                  hybrid_tfidf_probs  
0  [0.23367315624150653, 0.3188542931213096, 0.44...  
1  [0.21772001107917457, 0.30858230910860185, 0.4...  
2  [0.21621107872193918, 0.2931501517807278, 0.49...  
3  [0.18708066801123957, 0.3254286696422012, 0.48...  
4  [0.27190308227016163, 0.3106431771033703, 0.41...  

[5 rows x 23 columns]

In [49]:
articletest.to_csv("articletestdata_hybridoutput.csv", index=False)

In [50]:
articletestdata_hybridoutput = pd.read_csv("articletestdata_hybridoutput.csv")
articletestdata_hybridoutput.head()

index                                                url       q3  \
0      2  http://www.washingtonpost.com/opinions/dont-le...  Opinion   
1      4  http://www.breitbart.com/Big-Government/2013/1...  Opinion   
2      8  http://www.dailykos.com/story/2013/12/02/12595...     News   
3      9  http://www.nytimes.com/2013/05/24/us/politics/...     News   
4     11  http://www.latimes.com/news/local/la-me-cap-gu...    other   

   perceived primary.topic secondary.topic     democrat.vote  \
0          1  Civil Rights    Civil Rights           Neutral   
1          1  Civil Rights    Civil Rights           Neutral   
2          1  Civil Rights    Civil Rights  SomewhatPositive   
3          1  Civil Rights    Civil Rights           Neutral   
4          0  Civil Rights    Civil Rights           Neutral   

    republican.vote                                            article  \
0           Neutral  david cole is a professor of constitutional la...   
1           Neutral  u.s. immigration citizenship and immigration s...   
2  SomewhatNegative              the following irresponsible police...   
3           Neutral  an alternative possibility is that a bipartisa...   
4  SomewhatPositive  sacramento — “living in parallel universes,” i...   

   length  ...  isbiased  biascategories bias_magnitude  bias_text  \
0     600  ...         0               0            0.0     center   
1     600  ...         0               0            0.0     center   
2     498  ...         1               1            1.0       left   
3     372  ...         0               0            0.0     center   
4     600  ...         1              -1            0.5      right   

                                             content  pred_labels  \
0  david cole is a professor of constitutional la...            1   
1  u.s. immigration citizenship and immigration s...            2   
2              the following irresponsible police...            2   
3  an alternative possibility is that a bipartisa...            1   
4  sacramento — “living in parallel universes,” i...            1   

  hybrid_label hybrid_prob                                    hybrid_nn_probs  \
0            1    0.998456  [0.000621203682385385, 0.9984557628631592, 0.0...   
1            2    0.996456  [0.00017927114095073193, 0.003364395350217819,...   
2            2    0.981165  [0.00046024733455851674, 0.018374672159552574,...   
3            1    0.998758  [0.0005090124905109406, 0.9987584352493286, 0....   
4            1    0.536058  [0.002071336144581437, 0.5360579490661621, 0.4...   

                                  hybrid_tfidf_probs  
0  [0.23367315624150653, 0.3188542931213096, 0.44...  
1  [0.21772001107917457, 0.30858230910860185, 0.4...  
2  [0.21621107872193918, 0.2931501517807278, 0.49...  
3  [0.18708066801123957, 0.3254286696422012, 0.48...  
4  [0.27190308227016163, 0.3106431771033703, 0.41...  

[5 rows x 23 columns]

In [ ]:
sourcetest = pd.read_table("sourcelevel_test_dataset.csv", index_col=0)

In [ ]:
sourcetest

In [ ]:
test_dataset = pd.read_table("Article-Bias-Prediction-main/data/randomtestdata.csv", sep=',', index_col=0)
test_dataset["pred_labels"] = 4
test_dataset.to_csv("sourcelevel_test_dataset.csv", sep='\t')

In [ ]:
start = 0
space = 50
end = space

def interval(s, e):
    return(s+space, e+space)

MAX_LEN = 512
nepochs = 20
nbatch = 16

from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
tokenizer_transformer = XLNetTokenizer.from_pretrained('xlnet-large-cased')

def create_input_array(df, tokenizer):
    sentences = df.content.values

    input_ids = []
    attention_masks = []
    token_type_ids = []

    for sent in sentences:
        # `encode_plus` will:
        #   (1) Tokenize the sentence.
        #   (2) Prepend the `[CLS]` token to the start.
        #   (3) Append the `[SEP]` token to the end.
        #   (4) Map tokens to their IDs.
        #   (5) Pad or truncate the sentence to `max_length`
        #   (6) Create attention masks for [PAD] tokens.
        encoded_dict = tokenizer.encode_plus(
            sent,  # Sentence to encode.
            add_special_tokens=True,  # Add '[CLS]' and '[SEP]'
            max_length=MAX_LEN,  # Pad & truncate all sentences.
                pad_to_max_length=True,
                return_attention_mask=True,  # Construct attn. masks.
                return_tensors='tf',  # Return tf tensors.
            )

        # Add the encoded sentence to the list.
        input_ids.append(encoded_dict['input_ids'])

        # And its attention mask (simply differentiates padding from non-padding).
        attention_masks.append(encoded_dict['attention_mask'])

        token_type_ids.append(encoded_dict['token_type_ids'])

    input_ids = tf.convert_to_tensor(input_ids)
    attention_masks = tf.convert_to_tensor(attention_masks)
    token_type_ids = tf.convert_to_tensor(token_type_ids)


    return input_ids, attention_masks, token_type_ids
#     return input_ids, attention_masks

def convert_inputs_to_tf_dataset(inputs):
    # args.max_seq_len = 256
    ids = inputs[0][0]
    masks = inputs[0][1]
    token_types = inputs[0][2]

    ids = tf.reshape(ids, (-1, MAX_LEN))
    print("Input ids shape: ", ids.shape)
    masks = tf.reshape(masks, (-1, MAX_LEN))
    print("Input Masks shape: ", masks.shape)
    token_types = tf.reshape(token_types, (-1, MAX_LEN))
    print("Token type ids shape: ", token_types.shape)

    ids=ids.numpy()
    masks = masks.numpy()
    token_types = token_types.numpy()
#     return[ids]
#     return [ids, masks, token_types]
    return [ids, masks]



In [ ]:
from tensorflow.compat.v1.keras.backend import set_session
config = tf.compat.v1.ConfigProto()
config.gpu_options.allow_growth = True  # dynamically grow the memory used on the GPU
config.log_device_placement = True  # to log device placement (on which device the operation ran)
sess = tf.compat.v1.Session(config=config)
set_session(sess)

In [ ]:
# this could've been so much easier if .predict wasn't broken.
# Instead, we break up the data into manageable chunks for .predict_on_batch

In [ ]:
# pred_probs = []

for i in range(int(1300/space)):
    print(start,end)
    test_dataset = pd.read_table("sourcelevel_test_dataset.csv", index_col=0)
#     test_dataset = pd.read_table("test_dataset.csv",  index_col=0)
    test_section = test_dataset[start:end]
    test_labels = np.asarray(le.fit_transform(test_section['bias_text']))
    test_inputs = [create_input_array(test_section, tokenizer=tokenizer_transformer)]
    test_data = convert_inputs_to_tf_dataset(test_inputs)
    testmodel = TFXLNetForSequenceClassification.from_pretrained("data/experiments/XLNetmodellarge", num_labels=len(np.unique(test_labels)))
    loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
    metric = tf.keras.metrics.SparseCategoricalAccuracy('accuracy')
    optimizer = tf.keras.optimizers.Adam(learning_rate=2e-07, epsilon=1e-08)

    testmodel.compile(optimizer=optimizer, loss=loss, metrics=[metric])
#     test_probs = testmodel.predict_on_batch(test_data, batch_size= 5, verbose=0)
    nn_output = testmodel.predict_on_batch(test_data)
    nn_logits = nn_output["logits"]
    nn_probs = list(np.array(tf.nn.softmax(nn_logits)))
    print(nnprobs)
#     pred_probs.append(test_probs)
#     test_classes = np.argmax(test_probs, axis = 1)
    c=0
    for i in range(test_classes.shape[0]):
        if test_classes[i]==test_labels[i]:
            c+=1
    print("Test accuracy:")
    print(c/test_labels.shape[0])
    test_dataset["pred_labels"][start:end] = test_classes
    test_dataset.to_csv("sourcelevel_test_dataset.csv", sep='\t')
    
    start, end = interval(start,end)
    tf.keras.backend.clear_session()

In [ ]:
len(pred_probs)

In [ ]:
len(pred_probs[0])

In [ ]:
pred_probs[0].shape

In [ ]:
pred_probs_list = []

#list(np.array(tf.nn.softmax(pred_probs[0][0])))

for i in range(len(pred_probs)):
    prob_chunk = pred_probs[i]
    for ii in range(prob_chunk.shape[0]):
        pred_probs_list.append(list(np.array(tf.nn.softmax(pred_probs[i][ii]))))



In [ ]:
sourceleveltestdata = pd.read_table("sourcelevel_test_dataset.csv", index_col=0)
sourceleveltestdata["pred_probs"] = pd.Series(pred_probs_list)
sourceleveltestdata.head()

In [ ]:
sourceleveltestdata.to_csv("sourcelevel_test_dataset.csv", sep='\t')

In [ ]:
np.argmax(pred_probs_list, axis = 1)

In [ ]:
pred_probs_list

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import cohen_kappa_score
from sklearn.metrics import roc_auc_score
from sklearn.metrics import confusion_matrix

In [ ]:
# # accuracy: (tp + tn) / (p + n)
# accuracy = accuracy_score(test_labels, test_classes)
# print('Accuracy: %f' % accuracy)
# # precision tp / (tp + fp)
# precision = precision_score(test_labels, test_classes)
# print('Precision: %f' % precision)
# # recall: tp / (tp + fn)
# recall = recall_score(test_labels, test_classes)
# print('Recall: %f' % recall)
# # f1: 2 tp / (2 tp + fp + fn)
# f1 = f1_score(test_labels, test_classes)
# print('F1 score: %f' % f1)
 

In [ ]:
confusion_matrix(test_labels, test_classes)

In [ ]:
# train_section.to_csv("train_dataset.csv", sep='\t')
# val_section.to_csv("val_dataset.csv", sep='\t')
# test_section.to_csv("test_dataset.csv", sep='\t')

In [ ]:
# model.save_pretrained(save_path)

In [ ]:
tf.keras.backend.clear_session()